In [ ]:
import numpy as np
import csv
import os
import math

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly&response_type=code

Enter your authorization code:
4/3wFHyzUkxDFK-Q7Gn7TYY_wmobkOVRqK9UZptoK9it3Vj-hC54ua_rc
Mounted at /content/drive


In [ ]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int

In [ ]:
def GetFreq(AnnotData):
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      return AnnotData[cell_id][1].frame-AnnotData[cell_id][0].frame 
  return 1

In [ ]:
def CalculateMovements(AnnotData, Robustness, Frequency):
  SumMovements = 0
  SumDistances = 0
  NumElements = 0
  CellMovements = []

  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      prevx = AnnotData[cell_id][0].posx
      prevy = AnnotData[cell_id][0].posy
      StartFrame = AnnotData[cell_id][1].frame
      MaxDist = 0
      CurrentMovement = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
          CurrentMovement += np.sqrt(np.power(element.posx-prevx,2)+np.power(element.posy-prevy,2))
          NumElements += 1
          prevx = element.posx
          prevy = element.posy
          DistFromZeroPos = np.sqrt(np.power(element.posx-AnnotData[cell_id][0].posx,2)+np.power(element.posy-AnnotData[cell_id][0].posy,2))
          if DistFromZeroPos>MaxDist:
            MaxDist = DistFromZeroPos
        counter+=1
      SumDistances += MaxDist
      CellMovements.append(CurrentMovement)

  #Applying robust mean
  CellMovements.sort()
  if Robustness != 0:
    NumData = len(CellMovements)
    CellMovements = CellMovements[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumMovements = sum(CellMovements)

  SumMovements /= NumElements
  SumDistances /= NumElements
  return [SumMovements, SumDistances]

In [ ]:
def UnitVector(vector):
    return vector / np.linalg.norm(vector)

def AngleBetween(v1, v2):
    v1_u = UnitVector(v1)
    v2_u = UnitVector(v2)
    return np.arccos(np.clip(np.dot(v1_u, v2_u), -1.0, 1.0))

def CalculateAngles(AnnotData, Robustness, Frequency):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>2:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      StartFrame = AnnotData[cell_id][2].frame
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if counter>1 and np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
          Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])
          if not math.isnan(Angle):
            CurrentAngles += Angle
          pprevx = prevx
          pprevy = prevy
          prevx = element.posx
          prevy = element.posy
          NumElements += 1
        counter+=1
      CellAngles.append(CurrentAngles)

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumAngles = sum(CellAngles)/NumElements

  return [SumAngles]

def CalculateNormAngles(AnnotData, Robustness, Frequency):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>2:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      StartFrame = AnnotData[cell_id][2].frame
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if counter>1 and np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
          #Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])*(np.sqrt(np.power(pprevx-prevx,2)+np.power(pprevy-prevy,2))+np.sqrt(np.power(prevx-element.posx,2)+np.power(prevy-element.posy,2)))
          Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])*np.sqrt(np.power(pprevx-element.posx,2)+np.power(pprevy-element.posy,2))
          if not math.isnan(Angle):
            CurrentAngles += Angle
          pprevx = prevx
          pprevy = prevy
          prevx = element.posx
          prevy = element.posy
          NumElements += 1
        counter+=1
      CellAngles.append(CurrentAngles)

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumAngles = sum(CellAngles)/NumElements

  return [SumAngles]

In [ ]:
def ReadData(CellType, NameModifier, HumanDataFolder, ComputerDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  ComputerAnnotPath = ComputerDataFolder+CellType+NameModifier+".txt"

  HumanAnnotFile = open(HumanAnnotPath,"r") 
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 

  HumanAnnotList = HumanAnnotFile.readlines()
  ComputerAnnotList = ComputerAnnotFile.readlines()

  HumanAnnotData = {}
  ComputerAnnotData = {}

  for row in HumanAnnotList:
    splitted = row.split(' ')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3].strip())
      if not (cellp.id in HumanAnnotData):
        HumanAnnotData[cellp.id]=[]
        HumanAnnotData[cellp.id].append(cellp)
      else:
        HumanAnnotData[cellp.id].append(cellp)

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.frame = int(splitted[0].strip())
      cellp.id = int(splitted[1].strip())
      cellp.posx = int(splitted[2].strip())
      cellp.posy = int(splitted[3].strip())
      if not (cellp.id in ComputerAnnotData):
        ComputerAnnotData[cellp.id]=[]
        ComputerAnnotData[cellp.id].append(cellp)
      else:
        ComputerAnnotData[cellp.id].append(cellp)

  return[HumanAnnotData, ComputerAnnotData]
      

In [ ]:
#Listing all the videos in a folder

AvailableVideos = os.listdir('/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/01 Videos')
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_10
BIBF_01_16
BIBF_01_7
BIBF_03_16
BIBF_03_6
aktivin01_2
aktivin01_3
hipox03_2
melanoma_GF01_11
zometa01_4
zometa01_6
zometa02_4
zometa03_3
zometa03_5
zometa06_3


In [ ]:
#MAIN CODE

#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/02 Human Annotations/"
ComputerDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/03 Estimated Paths/"
OutCSVPath = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Results/Calculations.csv"
NameModifier= "_only_seedpoints"

with open(OutCSVPath, mode='w') as CSVfile:
  CSVwriter = csv.writer(CSVfile, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
  CSVwriter.writerow(['CellType','HumanAnnotatedMovements','HumanAnnotatedDistances','HumanAnnotatedNormAngles',
                      'ComputerAnnotatedMovements','ComputerAnnotatedDistances','ComputerAnnotatedNormAngles','ComputerAnnotatedNormAnglesWithFreq'])
  for CellType in CellTypes:
    #Reading both files
    [HumanAnnotData, ComputerAnnotData] = ReadData(CellType,NameModifier,HumanDataFolder,ComputerDataFolder)

    HumanAnnotFreq = GetFreq(HumanAnnotData)

    #Calculating the movements for both data
    [HumanSumMovements, HumanSumDistances] = CalculateMovements(HumanAnnotData,0,1)
    [ComputerSumMovements, ComputerSumDistances] = CalculateMovements(ComputerAnnotData,0,1)
    [ComputerSumMovementsFreq, ComputerSumDistancesFreq] = CalculateMovements(ComputerAnnotData,0,HumanAnnotFreq)
    [HumanSumAngles] = CalculateNormAngles(HumanAnnotData,0,1)
    [ComputerSumAngles] = CalculateNormAngles(ComputerAnnotData,0,1)
    [ComputerSumAnglesFreq] = CalculateNormAngles(ComputerAnnotData,0,HumanAnnotFreq)

    print(CellType)
    print("Human Annotation Frequency: "+str(HumanAnnotFreq))
    print("  "+str(HumanSumMovements))
    print("  "+str(ComputerSumMovements))
    print()
    print("  "+str(HumanSumDistances))
    print("  "+str(ComputerSumDistances))
    print()
    print("  "+str(HumanSumAngles))
    print("  "+str(ComputerSumAngles))
    print("  "+str(ComputerSumAnglesFreq))
    print()

    CSVwriter.writerow([CellType,HumanSumMovements,HumanSumDistances,HumanSumAngles,
                        ComputerSumMovements,ComputerSumDistances,ComputerSumAngles,ComputerSumAnglesFreq])

    

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: RuntimeWarning: invalid value encountered in true_divide
  


BIBF06_10
Human Annotation Frequency: 3
  3.9152728053792503
  2.4782130455599636

  1.1689887681539453
  0.9962359867876768

  2.1068344904573504
  3.64369966196448
  6.432500080948564

BIBF_01_16
Human Annotation Frequency: 3
  2.8323558215280102
  5.269992162890983

  0.6965926296495772
  1.657621924283407

  2.599531305492735
  9.7252071324896
  8.981036145547447

BIBF_01_7
Human Annotation Frequency: 3
  11.190917235821448
  9.47017624808957

  2.637192990369355
  2.3902874038245425

  10.50498387524229
  16.591248783981875
  25.541294378437446

BIBF_03_16
Human Annotation Frequency: 3
  11.202832773660766
  9.849032991184272

  3.24586400355857
  3.0370089423031104

  11.6611994833131
  17.540434451953296
  31.276047998323538

BIBF_03_6
Human Annotation Frequency: 3
  0.36855862402277556
  2.231471234257856

  0.11870965893570966
  0.15824516578977355

  0.19726730120890695
  3.832809777760211
  4.860430251944965

aktivin01_2
Human Annotation Frequency: 3
  4.179893400994439
  3.